In [6]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from sklearn.ensemble import RandomForestRegressor
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder, StandardScaler, OrdinalEncoder
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.multioutput import MultiOutputRegressor
from sklearn.ensemble import RandomForestRegressor    
import joblib

In [7]:
# Load
df = pd.read_csv("//Users/tanya-mac/Desktop/Health Risk Predictor from Lifestyle & Medical History/data/processed/final_data.csv")
print('Shape:', df.shape)
df.head()

Shape: (97297, 33)


Age  gender ethnicity education_level  income_level employment_status  \
0   58    Male     Asian      Highschool  Lower-Middle          Employed   
1   52  Female     White      Highschool        Middle          Employed   
2   60    Male  Hispanic      Highschool        Middle        Unemployed   
3   74  Female     Black      Highschool           Low           Retired   
4   46    Male     White        Graduate        Middle           Retired   

  smoking_status  alcohol_consumption_per_week  \
0          Never                             0   
1         Former                             1   
2          Never                             1   
3          Never                             0   
4          Never                             1   

   physical_activity_minutes_per_week  diet_score  ...  triglycerides  \
0                                 215         5.7  ...            145   
1                                 143         6.7  ...             30   
2                                  57         6.4  ...             36   
3                                  49         3.4  ...            140   
4                                 109         7.2  ...            160   

   glucose_fasting  glucose_postprandial  insulin_level  hba1c  \
0              136                   236           6.36   8.18   
1               93                   150           2.00   5.63   
2              118                   195           5.07   7.51   
3              139                   253           5.28   9.03   
4              137                   184          12.74   7.20   

   diabetes_risk_score  hypertension_risk_score  heart_disease_risk_score  \
0            51.716583                53.581369                 50.796020   
1            26.096162                47.946740                 23.853485   
2            54.830087                42.141104                 38.977694   
3            60.729521                60.286946                 53.579555   
4            32.778085                15.279074                 18.721942   

   obesity_risk_score  cholesterol_risk_score  
0           57.387241               51.492983  
1           36.219202                3.984993  
2           42.898797               21.793300  
3           52.194082               22.962029  
4           32.095465               34.296907  

[5 rows x 33 columns]

In [8]:
target_cols = [
    'diabetes_risk_score',
    'hypertension_risk_score',
    'heart_disease_risk_score',
    'obesity_risk_score',
    'cholesterol_risk_score'
]

# Split X and y
X = df.drop(columns=target_cols)
y = df[target_cols]

In [9]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.25, random_state=42
)

In [10]:
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder
# Categorical features
categorical_features_nominal = [
    'gender', 'ethnicity', 'employment_status', 'smoking_status'
]

categorical_features_ordinal = [
    'education_level', 'income_level'
]

# Define category orders
education_order = [["No formal", "Highschool", "Graduate", "Postgraduate"]]
income_order = [["Low", "Lower-Middle", "Middle", "Upper-Middle", "High"]]

# Preprocessor
preprocessor = ColumnTransformer(
    transformers=[
        ('ohe', OneHotEncoder(sparse_output=False, handle_unknown='ignore'),
         categorical_features_nominal),

        ('ord', OrdinalEncoder(categories=education_order + income_order),
         categorical_features_ordinal)
    ],
    remainder='passthrough'
)

In [11]:
# Model
base_rf = RandomForestRegressor(
    n_estimators=100,
    max_depth=12,
    max_features='sqrt',
    random_state=42,
    n_jobs=-1
)

In [12]:
multi_model = MultiOutputRegressor(base_rf, n_jobs=-1)

In [13]:
pipe = Pipeline([
    ('prep', preprocessor),
    ('model', multi_model)
])

# Train
pipe.fit(X_train, y_train)

# Predict
y_pred = pipe.predict(X_test)


In [14]:
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
# Compute metrics

metrics = {}
for i, col in enumerate(target_cols):
    mae = mean_absolute_error(y_test.iloc[:, i], y_pred[:, i])
    rmse = np.sqrt(mean_squared_error(y_test.iloc[:, i], y_pred[:, i] ))
    r2 = r2_score(y_test.iloc[:, i], y_pred[:, i])
    metrics[col] = {"MAE": mae, "RMSE": rmse, "R2": r2}
    print(f"{col} -> MAE: {mae:.3f}, RMSE: {rmse:.3f}, R2: {r2:.3f}")

# overall (mean MAE)
mean_mae = np.mean([m["MAE"] for m in metrics.values()])
print(f"Mean MAE across targets: {mean_mae:.3f}")

diabetes_risk_score -> MAE: 2.419, RMSE: 3.039, R2: 0.924
hypertension_risk_score -> MAE: 2.882, RMSE: 3.670, R2: 0.917
heart_disease_risk_score -> MAE: 3.858, RMSE: 4.855, R2: 0.901
obesity_risk_score -> MAE: 2.136, RMSE: 2.749, R2: 0.938
cholesterol_risk_score -> MAE: 1.817, RMSE: 2.460, R2: 0.965
Mean MAE across targets: 2.622


In [15]:
from lightgbm import LGBMRegressor
from sklearn.multioutput import MultiOutputRegressor

base_lgb = LGBMRegressor(
    n_estimators=500,
    learning_rate=0.05,
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42,
    n_jobs=-1
)

multi_model = MultiOutputRegressor(base_lgb, n_jobs=-1)

In [16]:
pipe_1 = Pipeline([
    ('preprocess', preprocessor),
    ('model', multi_model)
])

In [17]:
print("Fitting pipeline ...")
pipe_1.fit(X_train, y_train)
print("Training finished.")

Fitting pipeline ...
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.014841 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2711
[LightGBM] [Info] Number of data points in the train set: 72972, number of used features: 39
[LightGBM] [Info] Start training from score 41.234454
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.010243 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2711
[LightGBM] [Info] Number of data points in the train set: 72972, number of used features: 39
[LightGBM] [Info] Start training from score 48.393724
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003373 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[Li

In [18]:
y_pred_1 = pipe_1.predict(X_test)


/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  

In [19]:
metrics = {}
for i, col in enumerate(target_cols):
    mae = mean_absolute_error(y_test.iloc[:, i], y_pred_1[:, i])
    rmse = np.sqrt(mean_squared_error(y_test.iloc[:, i], y_pred_1[:, i] ))
    r2 = r2_score(y_test.iloc[:, i], y_pred_1[:, i])
    metrics[col] = {"MAE": mae, "RMSE": rmse, "R2": r2}
    print(f"{col} -> MAE: {mae:.3f}, RMSE: {rmse:.3f}, R2: {r2:.3f}")

# overall (mean MAE)
mean_mae = np.mean([m["MAE"] for m in metrics.values()])
print(f"Mean MAE across targets: {mean_mae:.3f}")

diabetes_risk_score -> MAE: 1.664, RMSE: 2.083, R2: 0.964
hypertension_risk_score -> MAE: 2.043, RMSE: 2.563, R2: 0.959
heart_disease_risk_score -> MAE: 3.227, RMSE: 4.101, R2: 0.929
obesity_risk_score -> MAE: 1.234, RMSE: 1.547, R2: 0.980
cholesterol_risk_score -> MAE: 0.823, RMSE: 1.030, R2: 0.994
Mean MAE across targets: 1.798


In [20]:
from xgboost import XGBRegressor

In [21]:
xgb = XGBRegressor(
    n_estimators=200,
    max_depth=7,
    learning_rate=0.05,
    subsample=0.8,
    colsample_bytree=0.8,
    tree_method="hist",
    n_jobs=1,
    random_state=42)

In [22]:
multi_model = MultiOutputRegressor(xgb, n_jobs=-1)

In [23]:
pipe_2 = Pipeline([
    ('preprocess', preprocessor),
    ('model', multi_model)
])

In [24]:
print("Fitting pipeline ...")
pipe_2.fit(X_train, y_train)
print("Training finished.")

Fitting pipeline ...
Training finished.


In [25]:
y_pred_2 = pipe_2.predict(X_test)  # shape (n_samples, 5)

In [26]:
metrics = {}
for i, col in enumerate(target_cols):
    mae = mean_absolute_error(y_test.iloc[:, i], y_pred_2[:, i])
    rmse = np.sqrt(mean_squared_error(y_test.iloc[:, i], y_pred_2[:, i] ))
    r2 = r2_score(y_test.iloc[:, i], y_pred_2[:, i])
    metrics[col] = {"MAE": mae, "RMSE": rmse, "R2": r2}
    print(f"{col} -> MAE: {mae:.3f}, RMSE: {rmse:.3f}, R2: {r2:.3f}")

# overall (mean MAE)
mean_mae = np.mean([m["MAE"] for m in metrics.values()])
print(f"Mean MAE across targets: {mean_mae:.3f}")

diabetes_risk_score -> MAE: 1.667, RMSE: 2.089, R2: 0.964
hypertension_risk_score -> MAE: 2.031, RMSE: 2.551, R2: 0.960
heart_disease_risk_score -> MAE: 3.237, RMSE: 4.109, R2: 0.929
obesity_risk_score -> MAE: 1.233, RMSE: 1.546, R2: 0.980
cholesterol_risk_score -> MAE: 0.832, RMSE: 1.044, R2: 0.994
Mean MAE across targets: 1.800


## Cross Validation

In [27]:
from sklearn.model_selection import KFold, cross_validate
from sklearn.metrics import make_scorer


# --------------------------
# Custom multi-output metrics
# --------------------------
def multi_mae(y_true, y_pred):
    y_true = np.asarray(y_true)
    y_pred = np.asarray(y_pred)
    return np.mean([mean_absolute_error(y_true[:, i], y_pred[:, i]) 
                    for i in range(y_true.shape[1])])

def multi_rmse(y_true, y_pred):
    y_true = np.asarray(y_true)
    y_pred = np.asarray(y_pred)
    return np.mean([np.sqrt(mean_squared_error(y_true[:, i], y_pred[:, i])) 
                    for i in range(y_true.shape[1])])

def multi_r2(y_true, y_pred):
    y_true = np.asarray(y_true)
    y_pred = np.asarray(y_pred)
    return np.mean([r2_score(y_true[:, i], y_pred[:, i]) 
                    for i in range(y_true.shape[1])])


# --------------------------
# Scoring dictionary
# --------------------------
scoring = {
    'mae': make_scorer(multi_mae, greater_is_better=False),
    'rmse': make_scorer(multi_rmse, greater_is_better=False),
    'r2': make_scorer(multi_r2, greater_is_better=True)
}

# --------------------------
# Cross-validation on TRAIN DATA ONLY
# --------------------------
cv = KFold(n_splits=5, shuffle=True, random_state=42)

cv_results = cross_validate(
    pipe_1,
    X_train,
    y_train,      # using only training data
    cv=cv,
    scoring=scoring,
    n_jobs=-1,
    return_train_score=False,
    error_score='raise'
)

# --------------------------
# Aggregate results
# --------------------------
mae_mean = -np.mean(cv_results['test_mae'])
mae_std  = np.std(cv_results['test_mae'])

rmse_mean = -np.mean(cv_results['test_rmse'])
rmse_std  = np.std(cv_results['test_rmse'])

r2_mean = np.mean(cv_results['test_r2'])
r2_std  = np.std(cv_results['test_r2'])

# --------------------------
# Final Output
# --------------------------
print(f"5-Fold CV MAE:  {mae_mean:.4f} ± {mae_std:.4f}")
print(f"5-Fold CV RMSE: {rmse_mean:.4f} ± {rmse_std:.4f}")
print(f"5-Fold CV R2:   {r2_mean:.4f} ± {r2_std:.4f}")

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.110397 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2696
[LightGBM] [Info] Number of data points in the train set: 58377, number of used features: 39
[LightGBM] [Info] Start training from score 32.071998
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002511 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2684
[LightGBM] [Info] Number of data points in the train set: 58378, number of used features: 39
[LightGBM] [Info] Start training from score 48.368518
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.072019 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total 

/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  

5-Fold CV MAE:  1.8007 ± 0.0039
5-Fold CV RMSE: 2.2694 ± 0.0031
5-Fold CV R2:   0.9653 ± 0.0002


## Hyperparameter Tuning

In [28]:
from sklearn.model_selection import RandomizedSearchCV, KFold
# -----------------------
# 1. Multi-output custom metrics (robust to pandas DataFrame y)
# -----------------------
def multi_mae(y_true, y_pred):
    y_true = np.asarray(y_true)
    y_pred = np.asarray(y_pred)
    return np.mean([
        mean_absolute_error(y_true[:, i], y_pred[:, i])
        for i in range(y_true.shape[1])
    ])

def multi_rmse(y_true, y_pred):
    y_true = np.asarray(y_true)
    y_pred = np.asarray(y_pred)
    return np.mean([
        np.sqrt(mean_squared_error(y_true[:, i], y_pred[:, i]))
        for i in range(y_true.shape[1])
    ])

def multi_r2(y_true, y_pred):
    y_true = np.asarray(y_true)
    y_pred = np.asarray(y_pred)
    return np.mean([
        r2_score(y_true[:, i], y_pred[:, i])
        for i in range(y_true.shape[1])
    ])

# scorers dictionary
scoring = {
    "mae": make_scorer(multi_mae, greater_is_better=False),
    "rmse": make_scorer(multi_rmse, greater_is_better=False),
    "r2": make_scorer(multi_r2, greater_is_better=True)
}

# -----------------------
# 2. Parameter space for LightGBM inside MultiOutputRegressor inside pipeline
# -----------------------
# IMPORTANT: this assumes your pipeline step name is exactly 'model'
# (as in: Pipeline(steps=[(...), ('model', MultiOutputRegressor(...))]))
# If your step has a different name, replace the 'model__' prefix with your step name + '__'
param_distributions = {
    "model__estimator__n_estimators": [200, 400, 600, 800],
    "model__estimator__learning_rate": [0.01, 0.03, 0.05, 0.07],
    "model__estimator__max_depth": [-1, 6, 8, 10],
    "model__estimator__num_leaves": [31, 40, 60, 80],
    "model__estimator__subsample": [0.7, 0.8, 0.9, 1.0],
    "model__estimator__colsample_bytree": [0.6, 0.7, 0.8, 0.9],
    "model__estimator__min_child_samples": [20, 30, 40],
    "model__estimator__reg_alpha": [0.0, 0.1, 0.3, 0.5],
    "model__estimator__reg_lambda": [0.0, 0.1, 0.3, 0.8, 1.0],
}

# -----------------------
# 3. RandomizedSearchCV setup
# -----------------------
cv = KFold(n_splits=3, shuffle=True, random_state=42)

random_search = RandomizedSearchCV(
    estimator=pipe_1,                   # your pipeline (must exist)
    param_distributions=param_distributions,
    n_iter=40,
    scoring=scoring,                    # multi-metric
    refit="mae",                        # final refit will use MAE
    cv=cv,
    verbose=2,
    n_jobs=-1,
    random_state=42
)

# -----------------------
# 4. Run hyperparameter tuning on TRAIN data only
# -----------------------
print("\nRunning RandomizedSearchCV (on X_train, y_train)...")
random_search.fit(X_train, y_train)
print("Tuning complete.\n")

# -----------------------
# 5. Print best params & CV scores (note MAE/RMSE are negative in cv_results_)
# -----------------------
print("Best parameters:")
for p, v in random_search.best_params_.items():
    print(f"  {p}: {v}")

best_idx = random_search.best_index_

# some CV result keys are 'mean_test_<scorer_name>'
mean_test_mae = random_search.cv_results_.get("mean_test_mae")
mean_test_rmse = random_search.cv_results_.get("mean_test_rmse")
mean_test_r2 = random_search.cv_results_.get("mean_test_r2")

print("\nBest CV scores (at best_index):")
if mean_test_mae is not None:
    print("  MAE :", -mean_test_mae[best_idx])   # negate because scorer returned negative
else:
    print("  MAE : (not available)")

if mean_test_rmse is not None:
    print("  RMSE:", -mean_test_rmse[best_idx])
else:
    print("  RMSE: (not available)")

if mean_test_r2 is not None:
    print("  R2  :", mean_test_r2[best_idx])
else:
    print("  R2  : (not available)")

# -----------------------
# 6. Retrieve tuned (refit) model and save it
# -----------------------
best_model = random_search.best_estimator_   # this is the pipeline refit on X_train,y_train with best params


Running RandomizedSearchCV (on X_train, y_train)...
Fitting 3 folds for each of 40 candidates, totalling 120 fits
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.037435 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2673
[LightGBM] [Info] Number of data points in the train set: 48648, number of used features: 39
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.030838 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2673
[LightGBM] [Info] Number of data points in the train set: 48648, number of used features: 39
[LightGBM] [Info] Start training from score 26.068208
[LightGBM] [Info] Start training from score 41.185140
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.041367 seconds.
You can set `force_row_wise=tru

/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[CV] END model__estimator__colsample_bytree=0.8, model__estimator__learning_rate=0.01, model__estimator__max_depth=8, model__estimator__min_child_samples=30, model__estimator__n_estimators=200, model__estimator__num_leaves=40, model__estimator__reg_alpha=0.0, model__estimator__reg_lambda=0.8, model__estimator__subsample=0.7; total time=  44.9s
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.007517 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.006696 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set 

/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  

[CV] END model__estimator__colsample_bytree=0.8, model__estimator__learning_rate=0.01, model__estimator__max_depth=8, model__estimator__min_child_samples=30, model__estimator__n_estimators=200, model__estimator__num_leaves=40, model__estimator__reg_alpha=0.0, model__estimator__reg_lambda=0.8, model__estimator__subsample=0.7; total time=  57.1s
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing row-wise multi-threadi

...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
/opt/anaconda3/envs/main/lib/python3.13/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  

[CV] END model__estimator__colsample_bytree=0.7, model__estimator__learning_rate=0.07, model__estimator__max_depth=10, model__estimator__min_child_samples=40, model__estimator__n_estimators=600, model__estimator__num_leaves=80, model__estimator__reg_alpha=0.3, model__estimator__reg_lambda=1.0, model__estimator__subsample=0.8; total time= 2.0min
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002647 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2711
[LightGBM] [Info] Number of data points in the train set: 72972, number of used features: 39
[LightGBM] [Info] Start training from score 48.393724
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003949 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] To

In [29]:
# Save the pipeline (includes preprocessors + MultiOutputRegressor)
joblib.dump(best_model, "best_pipeline.joblib")
print("\nSaved refit pipeline to: best_pipeline.joblib")


Saved refit pipeline to: best_pipeline.joblib
